# **Обучение CIFAR классификатора**

## **Введение**


В этом туториале мы рассмотрим, как обучить классификатор цветных изображений на 10 классов.

Рекомендуется сперва пройти [Обучение MNIST классификатора](https://puzzlelib.org/ru/tutorials/getting_started/TrainingMNIST/).

## **Обучающая выборка**

Скачаем датасет CIFAR c [оригинального сайта университета Торонто](http://www.cs.toronto.edu/~kriz/cifar.html), где был собран этот датасет. Этот датасет состоит из 60000 цветных изображений размера 32 на 32. На каждом изображении представлен объект одного из десяти типов: самолёт, автомобиль, птица, кошка, олень, собака, лягушка, лошадь, корабль, грузовик. На каждый класс приходится ровно 6000 изображений.

При помощи восклицательного знака мы можем пользоваться терминальными командами:

In [ ]:
!wget http://www.cs.toronto.edu/~kriz/cifar-10-python.tar.gz

Распакуем скачанные файлы:

In [ ]:
!tar -xf cifar-10-python.tar.gz

<figure>
<center>
<img src='https://i.postimg.cc/VLXWc8n8/cifar.png'/>
<figcaption><i>100 изображений для всех 10 категорий из датасета CIFAR-10</i></figcaption></center>
</figure>

Этот датасет, как и MNIST, считается одним из базовых в машинном обучении: на нём тестируются различные методы машинного обучения до того, как их можно будет масштабировать.

### **Реализация инструментами библиотеки**

Для дальнейшей работы необходимо:
- в настройках ноутбука поменять 'Hardware accelerator = GPU';
- установить пакет `colorama`;
- клонировать гитхаб; 
- поменять текущую директорию; 
- установить библиотеку с нужным бэкендом (в нашем случае `cuda`).

In [ ]:
!pip install colorama
!git clone https://github.com/puzzlelib/PuzzleLib

!cd PuzzleLib && python setup.py install --backend=cuda

Начало этого туториала практически такое же, как и для MNIST туториала:



In [ ]:
import os
import math

import numpy as np

from PuzzleLib.Datasets import Cifar10Loader

from PuzzleLib.Containers import Sequential
from PuzzleLib.Modules import Conv2D, MaxPool2D, Activation, Flatten, Linear
from PuzzleLib.Modules.Activation import relu
from PuzzleLib.Handlers import Trainer, Validator
from PuzzleLib.Optimizers import MomentumSGD
from PuzzleLib.Cost import CrossEntropy

from PuzzleLib.Visual import showImageBasedFilters, showFilters

Появились новые импорты библиотеки `math` и функции `showImageBasedFilters` - их появление мы объясним дальше. Также в импортах присутствует загрузчик CIFAR `Cifar10Loader`, аналогичный по смыслу загрузчику MNIST.

Загрузим данные:

In [ ]:
path = "./"
cifar10 = Cifar10Loader()
data, labels = cifar10.load(path=path)
data, labels = data[:], labels[:]
print("Loaded cifar10")

np.random.seed(1234)

<figure>
<center>
<img src='https://i.postimg.cc/nhRQdzcM/Screenshot-2020-10-22-at-20-08-59.png'/>
</figure>

## **Построение сети**

Для соединения модулей между собой здесь используется контейнер [Sequential](https://puzzlelib.org/ru/documentation/base/containers/Sequential/):

In [ ]:
seq = Sequential()

"""
А дальше начинаются первые отличия от MNIST туториала, на которые стоит обратить пристальное внимание. 
Архитектура сети будет примерно такой же, но обратите внимание на набор параметров у модулей:
"""
seq.append(Conv2D(3, 32, 5, pad=2, wscale=0.0001, initscheme="gaussian"))


Параметр `pad` (паддинг) говорит [свёрточному](https://puzzlelib.org/ru/documentation/base/modules/ConvND/) слою, какой отступ по сторонам от фотографии нужно сделать. Т. е. в этом случае фотография увеличивается на 2 пикселя слева, справа, сверху и снизу, новые пиксели заполняются нулями (это верно для каждой из карт входных данных, т. е. в случае RGB каждая из карт R, G и B будет увеличена).

Нужно это, например, для того, чтобы лучше обработать края карты: ведь фильтр свёрточного слоя без паддинга упрётся в край фотографии. В случае с наличием паддинга, фильтру-окошку разрешается немного вылезти за пределы карты, захватив добавленные туда нули.

Параметры `wscale` и `initscheme` отвечают за то, какие значения будут у весов создаваемого слоя в самом начале, до обучения. Значение "gaussian" сообщит слою, что нужно взять веса случайными нормальными, с дефолтным средним 0.0, а дисперсия будет взята равной `wscale`.

Почему здесь выбраны такие параметры? Примерно такая архитектура была придумана Крижевским (конкретно этот вариант идёт под лозунгом ["26% за 80 секунд на Fermi-поколении Nvidia GPU"](https://code.google.com/p/cuda-convnet/)).

Добавляем [макспул](https://puzzlelib.org/ru/documentation/base/modules/MaxPool2D/) с параметрами, отличающихся от параметров по умолчанию:

In [ ]:
seq.append(MaxPool2D(size=3, stride=2))

"""
Первый параметр - это размер фильтра, второй параметр - это шаг фильтра по фотографии. По дефолту они равны 2 и 2 соответственно.
"""

"""
Дальше всё без нововведений:
"""
seq.append(Activation(relu))

seq.append(Conv2D(32, 32, 5, pad=2, wscale=0.01, initscheme="gaussian"))
seq.append(MaxPool2D(size=3, stride=2))
seq.append(Activation(relu))

seq.append(Conv2D(32, 64, 5, pad=2, wscale=0.01, initscheme="gaussian"))
seq.append(MaxPool2D(size=3, stride=2))
seq.append(Activation(relu))

seq.append(Flatten())

А вот инициализация [линейного](https://puzzlelib.org/ru/documentation/base/modules/Linear/) слоя значительно отличается от MNIST туториала:

In [ ]:
seq.append(Linear(seq.dataShapeFrom((1, 3, 32, 32))[1], 64, wscale=0.1, initscheme="gaussian"))

Здесь размер линейного слоя устанавливается через то, что вернёт нам метод `dataShapeFrom`. Это метод, который есть у многих модулей нейронных слоёв: ему на вход передаётся размер входных данных (число изображений, число карт в изображении, высота карты, ширина карты), а на выходе он выдаёт размер данных после прохода через данный слой. Например, слой `Activation` при обращении к этому методу вернёт тот же размер, что в него был передан, так как слои активации не меняют размеров данных. А вот свёрточный слой или макспул-слой могут изменить размер данных.

Чтобы не ломать голову, какой получился размер данных перед входом в линейных слой, мы запросили у `seq` размер данных на выходе из него, после чего взяли компоненту размера №1 (размер - это 4 числа, например, (1, 3, 32, 32)): в этой компоненте после метода `Flatten` лежит полная размерность каждого из элементов данных (т.е. в компоненте №0 будет число обучающих образцов, в №1 - размер образца, в №2 - число 1, в №3 - число 1, так как Flatten всё расплющил).

На выходе от линейного слоя хотим вектор размера 64, инициализацию весов тоже указываем явно.

И наконец последние блоки сети:

In [ ]:
seq.append(Activation(relu))

seq.append(Linear(64, 10, wscale=0.1, initscheme="gaussian"))

## **Подготовка к обучению и обучение сети**

Выбор функции ошибки, оптимизатора и установка его на сеть:





In [ ]:
optimizer = MomentumSGD()
optimizer.setupOn(seq, useGlobalState=True)
optimizer.learnRate = 0.01
optimizer.momRate = 0.9

cost = CrossEntropy(maxlabels=10)

trainer = Trainer(seq, cost, optimizer)

validator = Validator(seq, cost)

Всё как и в туториале по MNIST, только появилась строчка:

In [ ]:
currerror = math.inf

Которая создаёт переменную `currerror`, в которую мы будем записывать ошибку сети на данных в каждой эпохе. Она нам пригодится для того, чтобы менять скорость обучения, `learnRate`, у нашего оптимизатора. Сперва поставили ошибку равной плюс бесконечности, так как хотим хоть с чем-то сравнить ошибку уже в нулевой эпохе обучения.

## **Обучение сети**

Запускаем обучение на 25 эпох:

In [ ]:
for i in range(25):
		trainer.trainFromHost(
			data[:50000], labels[:50000], macroBatchSize=50000,
			onMacroBatchFinish=lambda train: print("Train error: %s" % train.cost.getMeanError())
		)
		valerror = validator.validateFromHost(data[50000:], labels[50000:], macroBatchSize=10000)
		Accuracy = 1.0 - valerror
		print("Accuracy:", Accuracy)

		"""
		Далее идут строчки, которые раньше не встречались:
		"""
		if valerror >= currerror:
			optimizer.learnRate *= 0.5
			print("Lowered learn rate: %s" % optimizer.learnRate)

		"""
		Это эмпирическое правило, которое указывает, когда понижать скорость обучения.
		"""

		"""
		Далее, поскольку CIFAR - цветной, мы можем первый слой сети отобразить в цвете. 
		Т. е. для каждого из трёх каналов RGB мы берём соответствующие им фильтры, 
		после чего накладываем их друг на друга (фильтры R - как красные, G - как зелёную компоненту, B - голубую). 
		Сделать это можно только для первого слоя, так как дальше уже теряется привязка к одному из цветов RGB. 
		Эту процедуру отображения фильтров для первого слоя проводит метод `showImageBasedFilters`:
		"""
		currerror = valerror

		showImageBasedFilters(seq[0].W.get(), os.path.join(path, "conv1.png"))
	
		"""
		Кроме первого слоя, мы выводим в файл второй и третий свёрточный слои:
		"""
		showFilters(seq[3].W.get(), os.path.join(path, "conv2.png"))
		showFilters(seq[6].W.get(), os.path.join(path, "conv3.png"))


После 25 эпох обучения получаются вот такие изображения:

In [ ]:
from PIL import Image 
import matplotlib.pyplot as plt
import cv2
%matplotlib inline

def imshow(image_path, title=None, figsize = (25,1)):
  image = cv2.imread(image_path)
  image = cv2.cvtColor(image,cv2.COLOR_BGR2RGB)
  fig = plt.figure(figsize=figsize)
  ax = fig.add_subplot(1, 1, 1) 
  ax.axis('off')
  ax.set_title(image_path)
  ax.imshow(image)
  if title is not None:
    ax.set_title(f'{title}')

In [ ]:
imshow('conv1.png', title = 'Фильтры первого свёрточного слоя сети lenet (все 3x32 штуки в формате RGB)')

In [ ]:
imshow('conv2.png', title = 'Фильтры второго свёрточного слоя сети lenet (все 32x32 штуки в ч/б-формате)', figsize = (50,7))

In [ ]:
imshow('conv3.png', title = 'Фильтры третьего свёрточного слоя сети lenet (все 32x64 штуки в ч/б-формате)', figsize = (50,14))

Точность, с которой сеть научилась классифицировать изображения:

In [ ]:
print("Accuracy:", Accuracy)

Как видите, эта задача для нейронных сетей заметно сложнее, чем MNIST. Сеть смогла правильно определить всего 76% изображений.